In [ ]:
import pandas as pd
import numpy as np
import yfinance as yf
import statsmodels.api as sm
import matplotlib.pyplot as plt

from datetime import datetime
from google.colab import drive
from pandas_datareader import data as pdr
from sklearn.datasets import make_regression
from dateutil.relativedelta import relativedelta
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression, Lasso, LassoCV
from sklearn.metrics import accuracy_score, mean_absolute_error, mean_squared_error

drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
Training = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Train_big.csv', converters={'Global Company Key':str})

In [ ]:
Training.drop(Training.columns[-1], axis=1, inplace=True)

# Try different lambda values

In [ ]:
y_train = Training['Selected']
X_train = Training.drop(columns=['Selected'])

In [ ]:
alphas = np.logspace(-4, 2, 100)  # Varying lambda values logarithmically
model = LassoCV(alphas=alphas, cv=5)
model.fit(X_train, y_train)

best_alpha = model.alpha_

print("Best alpha (lambda):", best_alpha)

coefficients = model.coef_
intercept = model.intercept_

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.856389086275925, tolerance: 0.028916570771001147
  model = cd_fast.enet_coordinate_descent_gram(
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 7.941156877473361, tolerance: 0.028916570771001147
  model = cd_fast.enet_coordinate_descent_gram(
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 12.782275117805568, tolerance: 0.028916570771001147
  model = cd_fast.enet_coordinate_descent_gram(
/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_coordinate_descent.py:617: Conv

Best alpha (lambda): 100.0


# Run LASSO prediction with the best lambda

In [ ]:
Test = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/Test_small_filled_and_cleaned.csv', index_col=0, converters={'Global Company Key':str})

In [ ]:
model = Lasso(alpha=best_alpha)
model.fit(X_train, y_train)

predictions = model.predict(Test[X_train.columns])
Test['Selected'] = predictions

# Sort by 'Data Date' and 'Selected' and obtain Tickers of Top Quintile

In [ ]:
Test = Test.sort_values(by=['Data Date', 'Selected'], ascending = [True, False])

In [ ]:
def obtain_Ticker(group):
    return group.head(len(group) // 5)['Ticker Symbol'].tolist()

In [ ]:
# Group DataFrame by 'Data Date' and apply the custom function
Tickers = Test.groupby('Data Date').apply(obtain_Ticker)
Dates = Test['Data Date'].unique()

# Obtain Stock Price Data of Top Quintile

In [ ]:
replicating_portfolio1 = pd.DataFrame()

for i in range(350):
  print(i)
#for i in range(36):
  start_date = Dates[i]

  if (i+1) < len(Dates):
    end_date = (datetime.strptime(Dates[i+1], '%Y-%m-%d') + relativedelta(days=1)).strftime('%Y-%m-%d')
  else:
    end_date = (datetime.strptime(Dates[i], '%Y-%m-%d') + relativedelta(months=1) + relativedelta(days=1)).strftime('%Y-%m-%d')

  df = pd.DataFrame()
  print(start_date)
  print(end_date)

  for ticker in Tickers[i]:
    try:
      ticker_data = yf.download(ticker, start=start_date, end=end_date)['Adj Close']
      if not ticker_data.empty:
        df[ticker] = ticker_data
        df[ticker] = df[ticker].fillna(method='ffill')
        df[ticker] = df[ticker].pct_change()
        df['Equal_Weighted_Returns'] = df.mean(axis=1)
    except Exception as e:
      print('exception e')

  if not df.empty:
    replicating_portfolio1 = pd.concat([replicating_portfolio1, df['Equal_Weighted_Returns']], axis=0)

replicating_portfolio1

0
1983-09-30
1983-11-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
1
1983-10-31
1983-12-01
[*********************100%%**********************]  1 of 1 completed
2
1983-11-30
1984-01-01
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CCF']: Exception("%ticker%: Data doesn't exist for startDate = 439016400, endDate = 441781200")



3
1983-12-31
1984-02-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CVCO']: Exception("%ticker%: Data doesn't exist for startDate = 441694800, endDate = 444459600")



4
1984-01-31
1984-03-01
[*********************100%%**********************]  1 of 1 completed

...

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PXHI']: Exception("%ticker%: Data doesn't exist for startDate = 1348977600, endDate = 1351742400")



[*********************100%%**********************]  1 of 1 completed
349
2012-10-31
2012-12-01
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['UMAX']: Exception("%ticker%: Data doesn't exist for startDate = 1351656000, endDate = 1354338000")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%******

0
1983-09-30       NaN
1983-10-03  0.000000
1983-10-04 -0.012706
1983-10-05  0.000000
1983-10-06  0.000000
...              ...
2012-11-26 -0.012024
2012-11-27  0.028680
2012-11-28  0.009140
2012-11-29 -0.001514
2012-11-30  0.021033

[6641 rows x 1 columns]

In [ ]:
replicating_portfolio1.to_csv('LASSO_rep1.csv')

In [ ]:
replicating_portfolio2 = pd.DataFrame()

for i in range(350, len(Tickers)):
  print(i)
  start_date = Dates[i]

  if (i+1) < len(Dates):
    end_date = (datetime.strptime(Dates[i+1], '%Y-%m-%d') + relativedelta(days=1)).strftime('%Y-%m-%d')
  else:
    end_date = (datetime.strptime(Dates[i], '%Y-%m-%d') + relativedelta(months=1) + relativedelta(days=1)).strftime('%Y-%m-%d')

  df = pd.DataFrame()
  print(start_date)
  print(end_date)

  for ticker in Tickers[i]:
    try:
      ticker_data = yf.download(ticker, start=start_date, end=end_date)['Adj Close']
      if not ticker_data.empty:
        df[ticker] = ticker_data
        df[ticker] = df[ticker].fillna(method='ffill')
        df[ticker] = df[ticker].pct_change()
        df['Equal_Weighted_Returns'] = df.mean(axis=1)
    except Exception as e:
      print('exception e')

  if not df.empty:
    replicating_portfolio2 = pd.concat([replicating_portfolio2, df['Equal_Weighted_Returns']], axis=0)

replicating_portfolio2

350
2012-11-30
2013-01-01
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['ATVK']: Exception("%ticker%: Data doesn't exist for startDate = 1354251600, endDate = 1357016400")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['LRDR']: Exception("%ticker%: Data doesn't exist for startDate = 1354251600, endDate = 1357016400")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
351
2012-12-31
2013-02-01
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed

...

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['ATPC']: Exception("%ticker%: Data doesn't exist for startDate = 1688097600, endDate = 1690862400")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%******

ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['NBRVF']: Exception("%ticker%: Data doesn't exist for startDate = 1688097600, endDate = 1690862400")



[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%******

0
2012-11-30       NaN
2012-12-03 -0.000815
2012-12-04  0.001846
2012-12-05 -0.040542
2012-12-06  0.027125
...              ...
2023-10-24  0.002506
2023-10-25 -0.010011
2023-10-26 -0.000588
2023-10-27 -0.014740
2023-10-30  0.000816

[2684 rows x 1 columns]

In [ ]:
replicating_portfolio2.to_csv('LASSO_rep2.csv')

In [ ]:
#rep1 = pd.read_csv('LASSO_rep1.csv')
#rep2 = pd.read_csv('LASSO_rep2.csv')

rep1 = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/LASSO_rep1.csv')
rep2 = pd.read_csv('/content/drive/MyDrive/Senior Fall/Senior Thesis/Data/Separately/LASSO_rep2.csv')

In [ ]:
rep = pd.concat([rep1, rep2])
rep = rep.rename(columns ={'0': 'returns'})
rep = rep.dropna()
rep

Unnamed: 0   returns
1     1983-10-03  0.000000
2     1983-10-04 -0.012706
3     1983-10-05  0.000000
4     1983-10-06  0.000000
5     1983-10-07  0.000000
...          ...       ...
2679  2023-10-24  0.002506
2680  2023-10-25 -0.010011
2681  2023-10-26 -0.000588
2682  2023-10-27 -0.014740
2683  2023-10-30  0.000816

[8865 rows x 2 columns]

In [ ]:
rep.to_csv('LASSO_replicating.csv', index=False)